In [4]:
import pyodbc
import configparser
import pandas as pd
import numpy as np 
from datetime import datetime, time


config = configparser.ConfigParser()
config.read(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\CODIGOS\relatório_improdutivo\credenciais.ini")

# Conexão com o banco
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")

#gerar query
query = '''
SELECT 
    e.pdv,
    COALESCE(e.SKU_PARA, e.SKU) AS SKU_FINAL,
    MAX(e.[ESTOQUE ATUAL]) AS [ESTOQUE ATUAL],
    MAX(e.[ESTOQUE EM TRANSITO]) AS [ESTOQUE EM TRANSITO],
    MAX(e.[PEDIDO PENDENTE]) AS [PEDIDO PENDENTE],
    d.salescurve AS Curva,
    e.CATEGORIA,
    d.dayswithoutsales AS DiasSemVenda,
    d.nextcycleprojection,
    d.secondtonextcycleprojection
FROM 
    estoque_mar e  
LEFT JOIN draft d 
    ON d.loja_id = e.PDV 
   AND d.code = COALESCE(e.SKU_PARA, e.SKU)
WHERE 
    d.businessunit = 'EUD'
GROUP BY 
    e.pdv,
    COALESCE(e.SKU_PARA, e.SKU),
    d.salescurve,
    e.CATEGORIA,
    d.dayswithoutsales,
    d.nextcycleprojection,
    d.secondtonextcycleprojection
'''
df0 = pd.read_sql(query, conn)



C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_6076\879577847.py:48: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df0 = pd.read_sql(query, conn)


In [5]:
query_vendas = '''
SELECT 
	B.PDV, 
	B.SKU,
	B.DESCRICAO,
	SUM(CAST(b.VENDAS AS DECIMAL(18,2))) AS VENDAS_CICLO,
	C.Ciclo
FROM base_vendas_bi b
INNER JOIN ciclos_data_2025 c 
    ON CAST(b.[DATA] AS DATE) = CONVERT(DATE, c.[Date], 103) AND C.MARCA = 'BOT'
LEFT JOIN (
    SELECT SKU, MAX(ORIGEM) AS ORIGEM
    FROM estoque_mar
    GROUP BY SKU
) e ON b.SKU = e.SKU
WHERE b.[DATA] > '2024-07-28'
GROUP BY
B.PDV, 
	B.SKU,
	B.DESCRICAO,
	C.Ciclo,
	E.ORIGEM 
'''

dfv0 = pd.read_sql(query_vendas, conn)

conn.close()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_6076\1692316838.py:25: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  dfv0 = pd.read_sql(query_vendas, conn)


In [6]:
df=df0

In [7]:

# 1. Agrupamento
df_agrupado = dfv0.groupby(['PDV', 'SKU', 'DESCRICAO', 'Ciclo'], as_index=False)['VENDAS_CICLO'].sum()

# 2. Pivotar o DataFrame
df_pivotado = df_agrupado.pivot_table(
    index=['PDV', 'SKU', 'DESCRICAO'],
    columns='Ciclo',
    values='VENDAS_CICLO',
    fill_value=0  # Substitui NaN por 0
)

# 3. Resetar o índice para deixar como DataFrame normal (opcional)
df_vendas = df_pivotado.reset_index()

# 4. (Opcional) Renomear colunas com prefixo "Ciclo_"
df_vendas.columns.name = None
df_vendas = df_vendas.rename(columns=lambda x: f'Ciclo_{x}' if isinstance(x, (int, str)) and str(x).isdigit() else x)

# Resultado final
df_vendas


PDV    SKU                                DESCRICAO  C202411  \
0       11201   1004            FLORATTA DES COL MY BLUE 75ml      0.0   
1       11201   1005         DEM FLORATTA DES COL MY BLUE 4ml      0.0   
2       11201   1078          MATCH SRUM CAP POS QUIMICA 50ml      0.0   
3       11201   1296      PMPCK THE BLEND DES ANTIT AER 2x75g      0.0   
4       11201   1302           PMPCK LILY DES ANTIT AER 2x75g      0.0   
...       ...    ...                                      ...      ...   
188531   5699  90770       PIN BALAO O BOTICARIO PAIS/25 UNIT      0.0   
188532   5699  90772        PIN AMOR O BOTICARIO PAIS/25 UNIT      0.0   
188533   5699  90774  PIN MELHOR PAI O BOTICARIO PAIS/25 UNIT      0.0   
188534   5699  90776  SACOLA TOP M O BOTICARIO PAIS 2025 UNIT      0.0   
188535   8074  43151                     MATERIAL POS CONSUMO      0.0   

        C202412  C202413  C202414  C202415  C202416  C202417  ...  C202502  \
0           0.0      0.0      0.0      0.0      0.0      0.0  ...      0.0   
1           0.0      0.0      0.0      0.0      0.0      0.0  ...      0.0   
2           0.0      0.0      0.0      0.0      0.0      0.0  ...      0.0   
3           0.0      0.0      0.0      0.0      0.0      0.0  ...      0.0   
4           0.0      0.0      0.0      0.0      0.0      0.0  ...      0.0   
...         ...      ...      ...      ...      ...      ...  ...      ...   
188531      0.0      0.0      0.0      0.0      0.0      0.0  ...      0.0   
188532      0.0      0.0      0.0      0.0      0.0      0.0  ...      0.0   
188533      0.0      0.0      0.0      0.0      0.0      0.0  ...      0.0   
188534      0.0      0.0      0.0      0.0      0.0      0.0  ...      0.0   
188535      0.0      0.0      0.0      0.0      0.0      0.0  ...      0.0   

        C202503  C202504  C202505  C202506  C202507  C202508  C202509  \
0           0.0      0.0      0.0      0.0      0.0      0.0      0.0   
1           0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2           0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3           0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4           0.0      0.0      0.0      0.0      0.0      0.0      0.0   
...         ...      ...      ...      ...      ...      ...      ...   
188531      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
188532      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
188533      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
188534      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
188535      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

        C202510  C202511  
0           0.0      0.0  
1           0.0      0.0  
2           0.0      0.0  
3           0.0      0.0  
4           0.0      0.0  
...         ...      ...  
188531      0.0      0.0  
188532      0.0      0.0  
188533      0.0      0.0  
188534      0.0      0.0  
188535      0.0      0.0  

[188536 rows x 21 columns]

In [8]:
# O QUE PRECISA PRA RODAR ESSE CÓDIGO:

# Arquivo Draft
# Arquivo Estoque
# Arquivo BI preço
# Arquivo pdv
# Arquivo Calendario
# Arquivo tabela de compra

#Atualizar o nome da marca no filtro do estoque.

In [9]:
# Caminho onde estão as subpastas com os arquivos CSV

# Set the path to the folder containing CSV files
#folder_path = r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\EUDORA\C13\DRAFT"   # arquivo dos drafts

# Pattern to match all CSV files
#csv_files = glob.glob(os.path.join(folder_path, '*.csv'))

# Read and concat all CSVs
#df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)


#df_draft.shape


In [10]:


#Caminho onde estão as subpastas com os arquivos CSV
#pasta_entrada =  r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\EUDORA\C13\estoque"

# Lista todas as subpastas dentro de "ESTOQUE"
#subpastas = [os.path.join(pasta_entrada, d) for d in os.listdir(pasta_entrada) if os.path.isdir(os.path.join(pasta_entrada, d))]

#df_list = []

# Percorre todas as subpastas
#for subpasta in subpastas:
#    arquivos = [f for f in os.listdir(subpasta) if f.endswith(".csv")]
#    nome_pasta = os.path.basename(subpasta)  # Obtém o nome da pasta

#    for arquivo in arquivos:
#        caminho_arquivo = os.path.join(subpasta, arquivo)
#        try:
#            df = pd.read_csv(caminho_arquivo, encoding="utf-8", low_memory=False)  # Melhor para grandes volumes de dados
#            df["Arquivo_Origem"] = arquivo  # Adiciona o nome do arquivo de origem
#            df["Pasta_Origem"] = nome_pasta  # Adiciona o nome da pasta de origem
#            df_list.append(df)
#        except Exception as e:
#            print(f"Erro ao ler o arquivo {arquivo}: {e}")

#if df_list:
#    df_estoque = pd.concat(df_list, ignore_index=True)

#df_estoque['PDV'] = df_estoque['PDV'].astype(str)

#df_estoque['SKU_FINAL'] = np.where(df_estoque['SKU_PARA'] == "-", df_estoque['SKU'], df_estoque['SKU_PARA'])

#df_estoque['SKU_FINAL']=df_estoque['SKU_FINAL'].astype(str)'''


In [11]:
df_bi_preco = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\EUDORA\202511\preço BI\TABELA DE PREÇOS (2).xlsx")

c:\Users\joao.herculano\AppData\Local\Programs\Python\Python313\Lib\site-packages\openpyxl\styles\stylesheet.py:237: UserWarning: Workbook contains no default style, apply openpyxl's default
  warn("Workbook contains no default style, apply openpyxl's default")


In [12]:
df_bi_preco.columns

Index(['SKU1', 'SKU2', 'Descrição', 'MARCA', 'CATEGORIA', 'LINHA', 'UF',
       'Tipo Preço', 'PC', 'PV'],
      dtype='object')

In [13]:
df_pdv = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")
df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})
df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO', 'SUPERVISOR', 'STATUS'])
df_pdv = df_pdv[~df_pdv['CANAL'].isin(['MTZ','LJ'])]




In [14]:
df_pdv['PDV'].value_counts()

PDV
20968    1
20969    1
20970    1
20986    1
20988    1
20989    1
20991    1
20992    1
20993    1
20994    1
20995    1
20996    1
20997    1
20998    1
20999    1
21000    1
21001    1
21278    1
21375    1
21383    1
21495    1
22448    1
22541    1
23703    1
23704    1
23711    1
23712    1
24255    1
24257    1
24269    1
24293    1
23813    1
Name: count, dtype: int64

In [15]:
df_pdv['MATCH'] = 1

**ALTERAR NOME DA COLUNA "ARQUIVO_ORIGEM" PARA UMA DAS OPÇÕES ABAIXO:**

*BOT.csv* 

*EUD.csv*

*QDB.csv*

In [16]:
#df_estoque = df_estoque[df_estoque['Arquivo_Origem']== "EUD.csv"]

In [17]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")

In [18]:
calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)
calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]


calendario = calendario[calendario['MARCA'] == "EUDORA"]

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 2).astype(str).str.zfill(2)

ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]


# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]


filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)



In [19]:
filtered_calendario

Ciclo INICIO CICLO  FIM CICLO  DURAÇÃO   MARCA       Date  NUM_CICLO  \
2346  C202513   2025-08-27 2025-09-16       21  EUDORA 2025-08-27         13   

     ANO_CICLO CICLOMAIS2  dias_ate_inicio  
2346     C2025    C202515               29

In [20]:
filtered_calendario['match'] = 1

In [21]:
df_pdv['UF'] = np.where(df_pdv['UF'] == 'VDC','BA',df_pdv['UF'])

In [22]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\EUDORA\202513\tabela promo\TABELA-DE-PROMOS_C13-(1)-1752011522504.xlsx.xlsx",skiprows=1)


In [23]:
df_tabela

Ciclo    Veiculo Tipo de Promoção Estratégia de Promoção  \
0    202513    Guia CF      Promoção CF        Movimentar Flow   
1    202513    Guia CF      Promoção CF        Movimentar Flow   
2    202513    Guia CF      Promoção CF        Movimentar Flow   
3    202513    Guia CF      Promoção CF        Movimentar Flow   
4    202513    Guia CF      Promoção CF        Movimentar Flow   
..      ...        ...              ...                    ...   
345  202513  Fora Guia      Promoção RE        Movimentar Flow   
346  202513  Fora Guia      Promoção RE        Movimentar Flow   
347  202513  Fora Guia      Promoção RE        Movimentar Flow   
348  202513  Fora Guia      Promoção RE        Movimentar Flow   
349  202513  Fora Guia      Promoção RE        Movimentar Flow   

       Tipo_mecanica Promo Período Limitado?  EAM       Categoria  Cód. Combo  \
0    Desconto Direto                     NaN  Não  PERF. FEMININA         NaN   
1    Desconto Direto                     NaN  Não  PERF. FEMININA         NaN   
2    Desconto Direto                     NaN  Não  PERF. FEMININA         NaN   
3    Desconto Direto                     NaN  Não  PERF. FEMININA         NaN   
4    Desconto Direto                     NaN  Não  PERF. FEMININA         NaN   
..               ...                     ...  ...             ...         ...   
345  Desconto Direto              Ciclo todo  Não         CABELOS         NaN   
346  Desconto Direto              Ciclo todo  Não         CABELOS         NaN   
347  Desconto Direto              Ciclo todo  Não         CABELOS         NaN   
348  Desconto Direto              Ciclo todo  Não         CABELOS         NaN   
349  Desconto Direto              Ciclo todo  Não         CABELOS         NaN   

     Código do Item  ... 0.34.2 0.35.2  0.2.3  0.25.3  0.28.3  0.3.3  0.32.3  \
0             85268  ...  59.47  61.22    0.2    0.25    0.28    0.3    0.32   
1             93541  ...  30.57  31.47    0.2    0.25    0.28    0.3    0.32   
2             53138  ...  35.67  36.72    0.2    0.25    0.28    0.3    0.32   
3             50762  ...  23.43  24.12    0.2    0.25    0.28    0.3    0.32   
4             49803  ...  28.53  29.37    0.2    0.25    0.28    0.3    0.32   
..              ...  ...    ...    ...    ...     ...     ...    ...     ...   
345           53094  ...   0.00   0.00    NaN     NaN     NaN    NaN     NaN   
346           55803  ...   0.00   0.00    NaN     NaN     NaN    NaN     NaN   
347           93106  ...   0.00   0.00    NaN     NaN     NaN    NaN     NaN   
348           93105  ...   0.00   0.00    NaN     NaN     NaN    NaN     NaN   
349           55805  ...   0.00   0.00    NaN     NaN     NaN    NaN     NaN   

     0.34.3  0.35.3  BSO  
0      0.34    0.35  Sim  
1      0.34    0.35  Sim  
2      0.34    0.35  Sim  
3      0.34    0.35  Sim  
4      0.34    0.35  Sim  
..      ...     ...  ...  
345     NaN     NaN  Sim  
346     NaN     NaN  Sim  
347     NaN     NaN  Sim  
348     NaN     NaN  Sim  
349     NaN     NaN  Sim  

[350 rows x 47 columns]

In [24]:
df_tabela = df_tabela[[    'Ciclo',                 'Veiculo',
              'Tipo de Promoção',  'Estratégia de Promoção',
                 'Tipo_mecanica', 'Promo Período Limitado?',
                           'EAM',               'Categoria',
                    'Cód. Combo',          'Código do Item',
             'Descrição do Item',     'Chamada Promocional',
                 'Valor do Guia',      'Preço Promocionado',
                 '% de Desconto',           'RE compra por',
                  'RE Vende por',          'RE lucra  (R$)']]

In [25]:
df_tabela['Código do Item'] = df_tabela['Código do Item'].astype(str).str.replace(".0","",regex=False)

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_6076\2370731253.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_tabela['Código do Item'] = df_tabela['Código do Item'].astype(str).str.replace(".0","",regex=False)


In [26]:
df_tabela['MATCH'] = 1

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_6076\1166075419.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_tabela['MATCH'] = 1


In [27]:
df_tabela = pd.merge(left=df_tabela,right=df_pdv[['PDV','MATCH','UF','DESCRIÇÃO PDV','ANALISTA']],on='MATCH',how='inner')

In [28]:
df_tabela = df_tabela.drop_duplicates()

In [29]:
df_tabela.columns

Index(['Ciclo', 'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA'],
      dtype='object')

In [30]:
df.columns

Index(['pdv', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection'],
      dtype='object')

In [31]:
df['pdv'] = df['pdv'].astype(str)

In [32]:
df['SKU_FINAL'] = df['SKU_FINAL'].astype(str)


In [33]:
df_tabela['Código do Item'] = df_tabela['Código do Item'].astype('str')

In [34]:
df_tabela['PDV'] = df_tabela['PDV'].astype(str)

In [35]:
df_final = pd.merge(left=df,right=df_tabela,right_on=['Código do Item','PDV'],left_on=['SKU_FINAL','pdv'],how='right')
df_final.shape  

(10656, 33)

In [36]:
df_final['match'] = 1

In [37]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','match','dias_ate_inicio']], on='match',how='inner')
df_final.shape

(10656, 39)

In [38]:
#df_final = pd.merge(left=df_final,right=df_pdv[['PDV', 'CANAL', 'DESCRIÇÃO PDV', 'PDV DESC','UF', 'MARCA', 'ANALISTA']],on = 'PDV',how='inner')
df_final.shape

(10656, 39)

In [39]:
#df_final['SKU'] = df_final['SKU'].astype(str) 
#df_final['PDV'] = df_final['PDV'].astype(str) 
#df_final = pd.merge(left=df_final,right=df_estoque[['SKU_FINAL', 'DDV PREVISTO', 'COBERTURA ATUAL','PDV']],right_on=['PDV','SKU_FINAL'],left_on=['PDV','SKU'],how='left')
#df_final.shape

In [40]:

df_bi_preco['SKU2'] = df_bi_preco['SKU2'].astype(str).str.replace('.0','',regex=False) 

df_final = pd.merge(left=df_final,right=df_bi_preco[['SKU2', 'UF','Tipo Preço', 'PC', 'PV']],right_on=['UF','SKU2'],left_on=['UF','SKU_FINAL'],how='left')
df_final.shape   

(10656, 43)

In [41]:
#df_bi_preco['SKU1'] = df_bi_preco['SKU1'].astype(str).str.replace('.0','',regex=False) 

#df_final = pd.merge(left=df_final,right=df_bi_preco[['SKU1', 'SKU2', 'UF', 'PC', 'PV']],right_on=['UF','SKU1'],left_on=['UF','SKU'],how='left')
#df_final.shape   

In [42]:
#df_bi_preco = df_bi_preco[df_bi_preco['MARCA']=='EUDORA']

In [43]:
#df_final['PRECO DE COMPRA'] = np.where(~df_final['PC_x'].isna(),df_final['PC_x'],df_final['PC_y'])

#df_final['PRECO DE VENDA'] = np.where(~df_final['PV_x'].isna(),df_final['PV_x'],df_final['PV_y'])



In [44]:
#df_estoque = df_estoque.rename(columns={'SKU_FINAL':'SKU_PARA_VALIDACAO'})
#df_final = pd.merge( left= df_final, right = df_estoque[['SKU_PARA_VALIDACAO','Arquivo_Origem']], left_on= 'SKU', right_on='SKU_PARA_VALIDACAO', how='left')

In [45]:
df_final.columns

Index(['pdv', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'SKU2',
       'Tipo Preço', 'PC', 'PV'],
      dtype='object')

In [46]:
#df_final = df_final.drop(columns=['Desativação','Lançamento','Promoção Próximo Ciclo','Compra inteligente semanal/Sugestão de compra','Planograma','Carteira Bloqueada Para Novos Pedidos','Preço Sell In','Quantidade','Item analisado','Promoção Próximo Ciclo + 1','SKU_PARA_VALIDACAO','Ciclo_y'])

In [47]:
df_final['PDV_SKU'] = df_final['PDV'].astype(str) + df_final['SKU_FINAL'].astype(str) 
df_final['UFPRODUTO'] = df_final['UF'].astype(str) + df_final['SKU_FINAL'].astype(str)

df_final.shape

(10656, 45)

In [48]:
df_final['nextcycleprojection'].value_counts()

df_final['secondtonextcycleprojection'].value_counts()

secondtonextcycleprojection
0.0      5042
1.0       237
3.0       210
2.0       162
4.0       104
         ... 
366.0       1
95.0        1
177.0       1
110.0       1
109.0       1
Name: count, Length: 126, dtype: int64

In [49]:
#df_final['PROJEÇÃO DO CICLO PROMOCIONADO'] =df_final['Projeção Próximo Ciclo + 1'] - df_final['Projeção Próximo Ciclo'] # projeção do ciclo em estudo

In [50]:
#df_final['PROJEÇÃO DO CICLO PROMOCIONADO'].value_counts()

In [51]:
#df_final['Data Prevista Regularização'] = df_final['Data Prevista Regularização'].astype(str).replace('0','REGULAR')

In [52]:
df_final = df_final.rename(columns={'Arquivo_Origem': 'MARCA'})

In [53]:
#df_final = df_final[~df_final['MARCA'].isna()]
#df_final['MARCA'].isna().sum()

In [54]:
df_final = df_final.drop_duplicates()
df_final.shape

(10656, 45)

In [55]:
df_final.columns

Index(['pdv', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'SKU2',
       'Tipo Preço', 'PC', 'PV', 'PDV_SKU', 'UFPRODUTO'],
      dtype='object')

In [56]:
df_vendas['PDV'] = df_vendas['PDV'].astype(str)
df_vendas['SKU'] = df_vendas['SKU'].astype(str)

df_vendas.columns

Index(['PDV', 'SKU', 'DESCRICAO', 'C202411', 'C202412', 'C202413', 'C202414',
       'C202415', 'C202416', 'C202417', 'C202501', 'C202502', 'C202503',
       'C202504', 'C202505', 'C202506', 'C202507', 'C202508', 'C202509',
       'C202510', 'C202511'],
      dtype='object')

In [57]:
df_final.shape

(10656, 45)

In [59]:
df_final = pd.merge(df_final,df_vendas,left_on=['pdv','SKU_FINAL'],right_on=['PDV','SKU'],how='inner')

In [60]:
df_final

pdv SKU_FINAL ESTOQUE ATUAL ESTOQUE EM TRANSITO PEDIDO PENDENTE Curva  \
0     20968     93541            23                   0               0     B   
1     20969     93541            27                   0               0     B   
2     20991     93541            20                   0               0     B   
3     20992     93541           178                   0               0     E   
4     20995     93541            67                   0               0     B   
...     ...       ...           ...                 ...             ...   ...   
3207  20998     53094           275                   0               0     A   
3208  21278     53094            38                   0               0     A   
3209  21495     53094             4                   0               0     A   
3210  22541     53094            46                   0               0     A   
3211  24255     53094             4                  56              25     E   

       CATEGORIA  DiasSemVenda  nextcycleprojection  \
0     PERFUMARIA          13.0                  0.0   
1     PERFUMARIA           3.0                  0.0   
2     PERFUMARIA           5.0                  0.0   
3     PERFUMARIA           0.0                  0.0   
4     PERFUMARIA           3.0                 14.0   
...          ...           ...                  ...   
3207     CABELOS           0.0                  0.0   
3208     CABELOS           0.0                  0.0   
3209     CABELOS           2.0                  0.0   
3210     CABELOS           2.0                  0.0   
3211     CABELOS           0.0                  0.0   

      secondtonextcycleprojection  ...  C202502 C202503 C202504 C202505  \
0                             0.0  ...      9.0     3.0     1.0     1.0   
1                             0.0  ...     18.0     3.0     8.0     9.0   
2                             0.0  ...     12.0     1.0     9.0    14.0   
3                           121.0  ...      0.0     0.0     0.0     0.0   
4                            53.0  ...     12.0    13.0     4.0    10.0   
...                           ...  ...      ...     ...     ...     ...   
3207                          0.0  ...    190.0   208.0    48.0    47.0   
3208                          0.0  ...     27.0    15.0    24.0    13.0   
3209                          0.0  ...      9.0     0.0     0.0     5.0   
3210                          0.0  ...      9.0     6.0     4.0    10.0   
3211                          0.0  ...      0.0     0.0     0.0     0.0   

     C202506 C202507 C202508 C202509  C202510 C202511  
0       21.0     3.0     1.0    13.0      1.0     1.0  
1       23.0     4.0     9.0     2.0     11.0     1.0  
2       16.0     6.0     8.0    26.0      9.0     1.0  
3        0.0     0.0     0.0     0.0      0.0     0.0  
4       43.0     8.0     6.0    27.0      1.0     2.0  
...      ...     ...     ...     ...      ...     ...  
3207   179.0    31.0    44.0    18.0    180.0    69.0  
3208    71.0    13.0     8.0    20.0     30.0    21.0  
3209     5.0     3.0     2.0     5.0      6.0     1.0  
3210    24.0    42.0     4.0     3.0      9.0     8.0  
3211     0.0     0.0     0.0     0.0      0.0     0.0  

[3212 rows x 66 columns]

In [61]:
df_final.columns

Index(['pdv', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV_x', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'SKU2',
       'Tipo Preço', 'PC', 'PV', 'PDV_SKU', 'UFPRODUTO', 'PDV_y', 'SKU',
       'DESCRICAO', 'C202411', 'C202412', 'C202413', 'C202414', 'C202415',
       'C202416', 'C202417', 'C202501', 'C202502', 'C202503', 'C202504',
       'C202505', 'C202506', 'C202507', 'C202508', 'C202509', 'C202510',
       'C2

In [62]:
# Define list of target columns
sales_2024_cols = df_final.columns[-18:-1]
# Create a new column with the row-wise max
df_final['PICO DE VENDAS 17CICLOS'] = df_final[sales_2024_cols].max(axis=1)



In [63]:
sales_2024_cols

Index(['C202411', 'C202412', 'C202413', 'C202414', 'C202415', 'C202416',
       'C202417', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506', 'C202507', 'C202508', 'C202509', 'C202510'],
      dtype='object')

In [64]:
vendas_6_meses = df_final.columns[-8:-2]

df_final['Pico Vendas Ultimos 6 ciclos'] = df_final[vendas_6_meses].max(axis=1)

In [65]:
df_final.columns[-19]

'C202412'

In [66]:
CRESCIMENTO = (df_final[df_final.columns[-18]].sum() - df_final[df_final.columns[-3]].sum())/df_final[df_final.columns[-18]].sum() 
print(CRESCIMENTO)

df_final['CRESCIMENTO'] = .2

0.3740666443775772


In [67]:
mesmo_ciclo_ano_passado = df_final.columns[-19]
ciclo_ano_passado = df_final.columns[-19:-18].str.split(" ")[0][-1]
df_final[ciclo_ano_passado] = df_final[mesmo_ciclo_ano_passado]

In [68]:
df_final.columns[-19:-18].str.split(" ")[0][-1]

'C202413'

In [69]:
df_final.columns[-21:-3]

Index(['C202411', 'C202412', 'C202413', 'C202414', 'C202415', 'C202416',
       'C202417', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506', 'C202507', 'C202508', 'C202509', 'C202510', 'C202511'],
      dtype='object')

In [70]:
vendas_todos_historicos = df_final.columns[-21:-3]

df_final['MEDIANA DO HISTÓRICO'] = df_final[vendas_todos_historicos].median(axis=1)

df_final['MEDIA DO HISTÓRICO'] = df_final[vendas_todos_historicos].mean(axis=1)

df_final['MEDIANA DO HISTÓRICO'] = np.where(df_final['MEDIANA DO HISTÓRICO'] <1,df_final['MEDIA DO HISTÓRICO'],df_final['MEDIANA DO HISTÓRICO'])


In [71]:
CRESCIMENTO

np.float64(0.3740666443775772)

In [72]:
df_final.columns

Index(['pdv', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV_x', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'SKU2',
       'Tipo Preço', 'PC', 'PV', 'PDV_SKU', 'UFPRODUTO', 'PDV_y', 'SKU',
       'DESCRICAO', 'C202411', 'C202412', 'C202413', 'C202414', 'C202415',
       'C202416', 'C202417', 'C202501', 'C202502', 'C202503', 'C202504',
       'C202505', 'C202506', 'C202507', 'C202508', 'C202509', 'C202510',
       'C2

In [73]:
df_final['PV GINSENG'] = np.where(df_final['CRESCIMENTO'] * df_final[ciclo_ano_passado] + df_final[ciclo_ano_passado] < df_final['MEDIANA DO HISTÓRICO'],
                                    np.ceil(df_final['CRESCIMENTO'] * df_final['MEDIANA DO HISTÓRICO']+ df_final['MEDIANA DO HISTÓRICO']), 
                                    np.ceil(df_final['CRESCIMENTO']*df_final[ciclo_ano_passado]+df_final[ciclo_ano_passado]))

In [74]:
#df_final['PV GINSENG'] = np.where(df_final['PV GINSENG']<1, df_final['Projeção Próximo Ciclo + 1'],df_final['PV GINSENG'])

In [75]:
#df_final = df_final.rename(columns={df_final.columns[18]: "C-4", df_final.columns[19]: "C-3",df_final.columns[20]: "C-2",df_final.columns[21]: "C-1"})

In [76]:
df_final.columns

Index(['pdv', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV_x', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'SKU2',
       'Tipo Preço', 'PC', 'PV', 'PDV_SKU', 'UFPRODUTO', 'PDV_y', 'SKU',
       'DESCRICAO', 'C202411', 'C202412', 'C202413', 'C202414', 'C202415',
       'C202416', 'C202417', 'C202501', 'C202502', 'C202503', 'C202504',
       'C202505', 'C202506', 'C202507', 'C202508', 'C202509', 'C202510',
       'C2

In [77]:
df_final.drop(columns=df_final.columns[-21:-10], inplace=True)

df_final.drop(columns=df_final.columns[-13:-11], inplace=True)


In [78]:
# List all columns except the two
cols_to_group_by = df_final.columns.difference(['DDV PREVISTO', 'COBERTURA ATUAL'])

# Group and aggregate
df_final_dedup = df_final
   

In [79]:
#df_final['Compra inteligente Próximo Ciclo']


In [80]:
#df_final['DDV PREVISTO'] = df_final['DDV PREVISTO'].fillna(0.01)


In [81]:
#df_final_dedup['DDV PREVISTO'] = np.where(
#    df_final_dedup['DDV PREVISTO'] == 0,
#    0.01,
#    df_final_dedup['DDV PREVISTO']
#)


In [82]:
#df_final_dedup['DDV PREVISTO'].value_counts()

In [83]:
#df_final_dedup['EST PROJE FINAL CICLO ATUAL'] = (df_final_dedup['Estoque Atual'] + df_final_dedup['Estoque em Transito']) - round(df_final_dedup['dias_ate_inicio'] * df_final_dedup['DDV PREVISTO'],0)

In [84]:
#df_final_dedup['EST PROJE FINAL CICLO ATUAL'] = np.where(df_final_dedup['EST PROJE FINAL CICLO ATUAL']<0,0,df_final_dedup['EST PROJE FINAL CICLO ATUAL'])

In [85]:
#df_final_dedup.columns

In [86]:
#df_final_dedup['VENDAS R$ PV GINSENG'] = df_final_dedup['PRECO DE VENDA'] * df_final_dedup['PV GINSENG']

In [87]:
#df_final_dedup = df_final_dedup.rename(columns={'Ciclo_x':'Ciclo'})

In [88]:
df_final_dedup['SUGESTÃO ABTASTECIMENTO	'] = ''
df_final_dedup['VENDAS R$ ABASTECIMENTO'] = ''


In [89]:
#df_final_dedup['RBV 202406'] = df_final_dedup['PRECO DE VENDA'] * df_final_dedup[ciclo_ano_passado] 

In [90]:
#df_final_dedup['COB PROJETADA'] = np.where(
#    df_final_dedup['DDV PREVISTO'] != 0,
#    (df_final_dedup['EST PROJE FINAL CICLO ATUAL'] + df_final_dedup['PV GINSENG']) / df_final_dedup['DDV PREVISTO'],
#    999)


In [91]:
#df_final_dedup.drop(columns=['dias_ate_inicio','SKU_FINAL','Projeção Próximo Ciclo + 1',
#                             'CRESCIMENTO'],inplace=True)

In [92]:
#df_final_dedup['MARCA'] = df_final_dedup['MARCA'].str.replace('.csv','',regex=False)

In [93]:
#df_final_dedup['COB PROJETADA'] = df_final_dedup['COB PROJETADA'].fillna(999)

In [94]:
#df_final_dedup.columns

In [95]:
#marca_promo =  df_estoque['Arquivo_Origem'].iloc[0].replace('.csv','')
#marca_promo

In [96]:
df_final.columns

Index(['pdv', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV_x', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'SKU2',
       'Tipo Preço', 'PC', 'PV', 'PDV_SKU', 'UFPRODUTO', 'PDV_y', 'SKU',
       'DESCRICAO', 'C202413', 'C202508', 'C202509', 'C202510', 'C202511',
       'PICO DE VENDAS 17CICLOS', 'Pico Vendas Ultimos 6 ciclos',
       'CRESCIMENTO', 'MEDIANA DO HISTÓRICO', 'MEDIA DO HISTÓRICO',
       'PV GINSENG', '

In [98]:
# Passo 1: ordenar
df_sorted = df_final.sort_values(by='% de Desconto', ascending=False)

# Passo 2: obter até 3 chamadas promocionais por grupo
promo_grouped = (
    df_sorted.groupby(['SKU_FINAL', 'pdv'])['Chamada Promocional']
    .apply(lambda x: x.dropna().unique()[:3])
    .apply(pd.Series)
    .rename(columns={0: 'MECÂNICA 1', 1: 'MECÂNICA 2', 2: 'MECÂNICA 3'})
    .reset_index()
)

# Passo 3: base com maior % de desconto
df_base = df_sorted.drop_duplicates(subset=['SKU_FINAL', 'pdv'], keep='first').reset_index(drop=True)

# Passo 4: merge com chamadas pivotadas
df_merged = df_base.merge(promo_grouped, on=['SKU_FINAL', 'pdv'], how='left')

# Corrigir dicionário: agrupar e pegar o primeiro valor válido por (SKU_FINAL, pdv)
# Passo 1: dicionário com Cód. Combo único por SKU_FINAL+pdv
cod_combo_map = (
    df_final
    .dropna(subset=['Cód. Combo'])
    .groupby(['SKU_FINAL', 'pdv'])['Cód. Combo']
    .first()
    .to_dict()
)

# Passo 2: gerar Series com os valores mapeados
cod_combo_series = df_merged.set_index(['SKU_FINAL', 'pdv']).index.map(cod_combo_map)

# Passo 3: substituir os valores diretamente
df_merged['Cód. Combo'] = cod_combo_series.where(cod_combo_series.notna(), df_merged['Cód. Combo'])



# Columns to bring up front
priority_cols = [
    'PDV_SKU',	'SKU',	'MARCA','INICIO CICLO',
    'FIM CICLO',	'DURAÇÃO','dias_ate_inicio',	
    'UFPRODUTO',	'Item Desativado',	'Data Prevista Regularização',
    'ANALISTA',	'UF',	'PDV',	'DESCRIÇÃO PDV',	'Classe',
    'Descrição','MECÂNICA 1',
       'MECÂNICA 2', 'MECÂNICA 3','Estoque Atual',	'COBERTURA ATUAL',
    'Estoque em Transito',	'Pedido Pendente',	'PICO DE VENDAS 2024','Pico Vendas Ultimos 6 ciclos',
    'C-4',	'C-3',	'C-2',	'C-1',	'Histórico de Vendas do Ciclo Atual',
    'Dias sem venda'
]

# All remaining columns
other_cols = [col for col in df_merged.columns if col not in priority_cols]

# Reorder
df_merged = df_merged[priority_cols + other_cols]


In [99]:
df_merged['INICIO CICLO'] = pd.to_datetime(df_merged['INICIO CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

df_merged['FIM CICLO'] = pd.to_datetime(df_merged['FIM CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

In [100]:
df_merged.columns

Index(['pdv', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV_x', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'SKU2',
       'Tipo Preço', 'PC', 'PV', 'PDV_SKU', 'UFPRODUTO', 'PDV_y', 'SKU',
       'DESCRICAO', 'C202413', 'C202508', 'C202509', 'C202510', 'C202511',
       'PICO DE VENDAS 17CICLOS', 'Pico Vendas Ultimos 6 ciclos',
       'CRESCIMENTO', 'MEDIANA DO HISTÓRICO', 'MEDIA DO HISTÓRICO',
       'PV GINSENG', '

In [101]:
df_merged = df_merged.loc[:, ~df_merged.columns.str.endswith('_y')]


In [102]:
df_merged.columns = df_merged.columns.str.replace('_x$', '', regex=True)


In [103]:
df_merged = df_merged.drop(columns=['Veiculo',	'Tipo de Promoção',	'Estratégia de Promoção','Tipo_mecanica'
                                    ,'Chamada Promocional','MATCH','match', 'SKU_FINAL','Descrição do Item','CRESCIMENTO',
                                    'Cód. Combo'])

In [104]:
df_merged['SUGESTÃO ANALISTA'] = ""

df_merged['SUGESTÃO COMERCIAL'] = ""

In [106]:
df_merged = df_merged.drop(columns=['Código do Item','PDV','RE compra por',	'RE Vende por',	'RE lucra  (R$)','INICIO CICLO',
                                    'FIM CICLO','SKU2','Tipo Preço','Ciclo','CATEGORIA','ANALISTA','dias_ate_inicio','PDV_SKU','UFPRODUTO',
                                    'VENDAS R$ ABASTECIMENTO','DURAÇÃO','MEDIANA DO HISTÓRICO','DURAÇÃO','PC','PV'])

In [107]:
df_merged = df_merged.rename(columns={'nextcycleprojection':'PROJEÇÃO PROX CICLO'	,'secondtonextcycleprojection':'PROJEÇÃO PROX CICLO +1'})

In [108]:
df_merged.columns = df_merged.columns.str.upper()

In [109]:
#df_merged = df_merged[['UF','PDV','DESCRIÇÃO PDV','SKU','DESCRICAO','EAM','CATEGORIA','CURVA','ESTOQUE ATUAL','ESTOQUE EM TRANSITO','PEDIDO PENDENTE','DIASSEMVENDA','PROJEÇÃO PROX CICLO','PROJEÇÃO PROX CICLO +1','PROMO PERÍODO LIMITADO?','VALOR DO GUIA','PREÇO PROMOCIONADO','% DE DESCONTO','PICO DE VENDAS 17CICLOS','PICO VENDAS ULTIMOS 6 CICLOS','MEDIA DO HISTÓRICO']]

In [110]:
df_merged['MEDIA DO HISTÓRICO'] = round(df_merged['MEDIA DO HISTÓRICO'],0)

In [111]:
df_merged.columns

Index(['PDV', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'CURVA', 'DIASSEMVENDA', 'PROJEÇÃO PROX CICLO',
       'PROJEÇÃO PROX CICLO +1', 'PROMO PERÍODO LIMITADO?', 'EAM', 'CATEGORIA',
       'VALOR DO GUIA', 'PREÇO PROMOCIONADO', '% DE DESCONTO', 'UF',
       'DESCRIÇÃO PDV', 'SKU', 'DESCRICAO', 'C202413', 'C202508', 'C202509',
       'C202510', 'C202511', 'PICO DE VENDAS 17CICLOS',
       'PICO VENDAS ULTIMOS 6 CICLOS', 'MEDIA DO HISTÓRICO', 'PV GINSENG',
       'SUGESTÃO ABTASTECIMENTO\t', 'MECÂNICA 1', 'MECÂNICA 2', 'MECÂNICA 3',
       'SUGESTÃO ANALISTA', 'SUGESTÃO COMERCIAL'],
      dtype='object')

In [112]:
# Colunas que devem estar na frente
colunas_inicio = [
    'UF', 'PDV', 'DESCRIÇÃO PDV', 'SKU', 'DESCRICAO', 'EAM', 'CATEGORIA', 'CURVA',
    'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DIASSEMVENDA',
    'PROJEÇÃO PROX CICLO', 'PROJEÇÃO PROX CICLO +1', 'PROMO PERÍODO LIMITADO?',
    'VALOR DO GUIA', 'PREÇO PROMOCIONADO', '% DE DESCONTO',
    'PICO DE VENDAS 17CICLOS', 'PICO VENDAS ULTIMOS 6 CICLOS', 'MEDIA DO HISTÓRICO'
]

# Colunas que devem estar no fim
colunas_fim = [
    'PV GINSENG', 'SUGESTÃO ABTASTECIMENTO\t', 'SUGESTÃO ANALISTA', 'SUGESTÃO COMERCIAL'
]

# Todas as outras colunas (não estão nem no início nem no fim)
colunas_meio = [col for col in df_merged.columns if col not in colunas_inicio + colunas_fim]

# Reordena o DataFrame
df_merged = df_merged[colunas_inicio + colunas_meio + colunas_fim]


In [113]:
df_merged = df_merged.drop_duplicates()

In [ ]:

from openpyxl import load_workbook
from openpyxl.styles import PatternFill, Font


# Export to Excel
output_file = f'C:\\Users\\joao.herculano\\Documents\\EUD_promoção_{ciclo_mais2}_04.06.xlsx'
with pd.ExcelWriter(output_file, engine='openpyxl') as writer:
    df_merged.to_excel(writer, index=False, sheet_name='Sheet1')

# Apply styles
wb = load_workbook(output_file)
ws = wb['Sheet1']

# Style header
header_fill = PatternFill(start_color='ADD8E6', end_color='ADD8E6', fill_type='solid')  # Light Blue
header_font = Font(color='FFFFFF', bold=True)  # White & Bold

for cell in ws[1]:
    cell.fill = header_fill
    cell.font = header_font

# Style rows: gray/white alternating
gray_fill = PatternFill(start_color='DDDDDD', end_color='DDDDDD', fill_type='solid')  # Light gray

for i, row in enumerate(ws.iter_rows(min_row=2, max_row=ws.max_row), start=2):
    if i % 2 == 0:
        for cell in row:
            cell.fill = gray_fill

# Save styled workbook
wb.save(output_file)


coisas q saem

Lançamento
Subcategoria
Projeção Próximo Ciclo 
Promoção Próximo Ciclo
Compra inteligente semanal/Sugestão de compra
Compra inteligente Próximo Ciclo
Planograma
Carteira Bloqueada Para Novos Pedidos
Quantidade por caixa
Preço Sell In
Quantidade
Item analisado
Tipo Preço

>>>>>>>>>>>>>NAO ESTÁ PEGANDO O MERGE COM O DF_ESTOQUE


CRIAR PROJEÇÃO DE VENDA DO CICLO ATUAL
Compra inteligente Próximo Ciclo + 1 >>>>>>> RENAME PRA NOROMAL